In [252]:
import pickle
# recommendation_data = pickle.load(open("top_n.pickle","rb"))
# with open("predictions_zscore.pickle", "rb") as file:
recommendation_data = pickle.load(open("predictions_zscore_revised.pickle","rb"))
recommendation_data = dict(recommendation_data) 

In [253]:
len(recommendation_data)

1117

In [254]:
recommendation_data[recommendation_data.keys()[-1]]

[('0451163524', 10),
 ('0439136350', 10),
 ('0439139597', 10),
 ('0385504209', 10),
 ('059035342X', 10),
 ('043935806X', 10),
 ('0451456734', 10),
 ('0671876015', 10),
 ('0872860175', 10),
 ('0439139600', 10)]

In [255]:
def get_book_details(ISBN):
    book_details = full_data[ISBN]
#     print(book_details)
    if 'Image-URL-S' in book_details.keys():
        del book_details['Image-URL-S']
    return full_data[ISBN]

In [256]:
import pandas as pd
import numpy as np

In [257]:
df = pd.read_csv("BX-Books.csv", sep = ';', error_bad_lines=False, encoding = 'latin-1')

Skipping line 6452: expected 8 fields, saw 9
Skipping line 43667: expected 8 fields, saw 10
Skipping line 51751: expected 8 fields, saw 9

Skipping line 92038: expected 8 fields, saw 9
Skipping line 104319: expected 8 fields, saw 9
Skipping line 121768: expected 8 fields, saw 9

Skipping line 144058: expected 8 fields, saw 9
Skipping line 150789: expected 8 fields, saw 9
Skipping line 157128: expected 8 fields, saw 9
Skipping line 180189: expected 8 fields, saw 9
Skipping line 185738: expected 8 fields, saw 9

Skipping line 209388: expected 8 fields, saw 9
Skipping line 220626: expected 8 fields, saw 9
Skipping line 227933: expected 8 fields, saw 11
Skipping line 228957: expected 8 fields, saw 10
Skipping line 245933: expected 8 fields, saw 9
Skipping line 251296: expected 8 fields, saw 9
Skipping line 259941: expected 8 fields, saw 9
Skipping line 261529: expected 8 fields, saw 9



In [258]:
df.columns = ['ISBN', 'BookTitle', 'BookAuthor', 'YearOfPublication', 'Publisher', 'Image-URL-S', 'ImageURLM', 'ImageURL']

In [259]:
dataset = pd.read_csv("train.csv")

In [260]:
len(dataset['User-ID'].unique())

1117

In [261]:
dataset.head()

Unnamed: 0  User-ID        ISBN  Book-Rating
0        1456   277427  002542730X           10
1        1465   277427  0060542128            7
2        1474   277427  0061009059            9
3        1522   277427  0316776963            8
4        1543   277427  0345413903           10

In [262]:
dict(dataset.iloc[1, [1, 2, 3]])

{'Book-Rating': 7, 'ISBN': '0060542128', 'User-ID': 277427}

In [263]:
full_data = {}

In [264]:
for record in df.to_dict(orient = 'records'):
    full_data[record['ISBN']] = record

In [265]:
get_book_details('0060542128')

{'BookAuthor': u'Heather Lowell',
 'BookTitle': u'When the Storm Breaks',
 'ISBN': u'0060542128',
 'ImageURL': u'http://images.amazon.com/images/P/0060542128.01.LZZZZZZZ.jpg',
 'ImageURLM': u'http://images.amazon.com/images/P/0060542128.01.MZZZZZZZ.jpg',
 'Publisher': u'HarperTorch',
 'YearOfPublication': 2003}

In [266]:
user_history = {}

## Generating Data for user-history

In [267]:
for i in range(len(dataset)):
    data = dict(dataset.iloc[i, [1, 2, 3]])
    user_id = data['User-ID']
    user_rating = data['Book-Rating']
    isbn = data['ISBN']
    book_details = get_book_details(isbn)
    if user_id not in user_history.keys():
        user_history[user_id] = []
    user_history[user_id].append(book_details)
#     else:
#         user_data[isbn] = []

In [268]:
for i in user_history.keys():
    for j in user_history[i]:
        if 'predicted_rating' in j.keys():
            print('hello')
            break
#         print j.keys()
#         break
#     break

In [269]:
data = dict(data)

## Getting User's fav authors

In [270]:
top_authors = {}
for user_id in user_history.keys():
    authors = []
    dict_authors = {}
    for book in user_history[user_id]:
        authors.append(book['BookAuthor'])
        if book['BookAuthor'] in dict_authors.keys():
            dict_authors[book['BookAuthor']] += 1
        else : dict_authors[book['BookAuthor']] = 1
#         break
#     print dict_authors
    top =  sorted(dict_authors.iteritems(), key=lambda (k,v): (v,k), reverse = True)[:5]
    top_authors[user_id] = [i for i, j in top]
# print top_authors
#     break
        

In [206]:
top_authors[131154]

[u'Terry Pratchett',
 u'J.R.R. TOLKIEN',
 u'Tim F. Lahaye',
 u'Nicholas Sparks',
 u'Lilian Jackson Braun']

In [207]:
combined_data = dataset.merge(df[['ISBN', 'BookAuthor']], on = "ISBN")

In [208]:
def check_in_history(isbn, userid):
    for book in user_history[user_id]:
        if book['ISBN'] == isbn:
#             print book
            return 0
    return 1

## Computing Average Rating for every book

In [209]:
avg_book_rating = {}
for isbn in combined_data['ISBN'].unique():
    mean = np.mean(combined_data[combined_data['ISBN'] == isbn]['Book-Rating'])
    if mean == np.nan : mean = 0
    else : avg_book_rating[isbn] = mean
best_books = sorted(avg_book_rating.items())[:10]

In [210]:
best_books_details = []
for isbn, rating in best_books:
    book_details = get_book_details(isbn)
    best_books_details.append(book_details)

## Getting the books by author_name

In [211]:
author_data = {}
for author_name in combined_data['BookAuthor'].unique():
    print author_name
    author_books_isbn =  combined_data[combined_data['BookAuthor'] == author_name]['ISBN'].values
    author_books_with_rating = []
    for book_isbn in author_books_isbn:
        author_books_with_rating.append((book_isbn, avg_book_rating[book_isbn]))

    author_books_with_rating.sort(key=lambda x: x[1], reverse = True)
    author_data[author_name] = author_books_with_rating

James Finn Garner
Heather Lowell
Janet Evanovich
David Sedaris
Jonathan Kellerman
Lynne Reid Banks
Sheri S. Tepper
John Grisham
Jon Krakauer
Margaret Atwood
Sebastian Junger
William Gerald Golding
Stephen King
Tom Clancy
Laura Childs
Danielle Steel
Perri O'Shaughnessy
HARLAN COBEN
JUDY BLUME
T. H. White
Allan Folsom
Ayn Rand
Greg Iles
Tracy Chevalier
Sue Grafton
LAURIE R. KING
Joseph R. Garber
John E. Douglas
Esther Friesner
Peter Mayle
Bradley Trevor Greive
Catherine Ryan Hyde
Camron Wright
Fern Michaels
Ruth Reichl
Dr. Jerri Nielsen
Nick Bantock
Scott Adams
Bill Watterson
Gary Larson
Richard Laymon
Sark
Martha Sacks
Lisa Scottoline
Stephen J. Cannell
ANNE PERRY
Karin Slaughter
Sandra Brown
Jan Burke
Catherine Coulter
Elizabeth George
Mary Higgins Clark
Ridley Pearson
Erica Spindler
Mary McGarry Morris
Helen Fielding
Beverley Donofrio
Alice Sebold
Patricia McCormick
JANE SMILEY
Dorothea Benton Frank
DEAN KOONTZ
Richard Paul Evans
Sidney Sheldon
Jodi Picoult
Tony Parsons
Betty J. Eadie

CHRISTINA SCHWARZ
Stephen L. Carter
Ernest J. Gaines
ANN PACKER
Michael J. Fox
Martha Moody
Zora Neale Hurston
Gail Godwin
CHARLES FRAZIER
Anna Quindlen
Nicole Mones
DAVE BARRY
Ann-Marie MacDonald
Karen Stolz
FANNIE FLAGG
Margaret George
LAURIE NOTARO
Linda Lay Shuler
Anne Frank
Maya Angelou
Michael Palmer
Arthur Hailey
Michael Connelly
SARAH L. DELANY
Mark Dunn
Adam Davies
Frank Mccourt
Matthew Thomas
Peter Hoeg
Geoff Ryman
Pamela Stephenson
James Rollins
Garth Nix
Antwone Q. Fisher
John Gray
Melissa Nathan
Jewel
John Colapinto
Barry Sears
Howard Stern
Mary Kay Andrews
Karyn Bosnak
Thornton Niven Wilder
Milan Kundera
David Feldman
Betty Smith
Kathryn Harrison
Eric Schlosser
Lily Prior
Oliver Sacks
Dog Mary Crow
E. L. Doctorow
Barbara Delinsky
Kevin J. Anderson
Barbara Michaels
Kyle Mills
Jeffrey Archer
Paulo Coelho
Susan G. Lydon
Frances Hodgson Burnett
Louise Fitzhugh
Francesca Lia Block
Gail Carson Levine
Lemony Snicket
Fannie Flagg
Philip Roth
Jerome Klapka Jerome
James Joyce
Joy K

Joan Anderson
Elaine St. James
Henry Miller
Gertrude Chandler Warner
N.E. Thing Enterprises
Jerry Jenkins
Editors Prevention Health Books
Oswald Chambers
Pamela Morsi
Dinah Mccall
Dalai Lama
RITA CIRESI
Tim Burton
Dan Millman
Erich Segal
ELLEN DEGENERES
Lynn Gordon
Patrick Lynch
Christine Feehan
Douglas Preston
Moon Unit Zappa
RICHARD NORTH PATTERSON
P.J. O'Rourke
T.S. Eliot
JAMES CLAVELL
J. F. Freedman
Daphne du Maurier
John Updike
David Fontana
PHILIP ROTH
Diana Gabaldon
ALICE HOFFMAN
Penelope Fitzgerald
Susan Orlean
Richard Ford
Jack Finney
DANIEL MASON
Russell Banks
Miguel Ruiz
TOM BROKAW
Christina Schwarz
Jane Moore
Lolly Winston
Vincent Lardo
Kazuo Ishiguro
Beverly Lewis
Malachy McCourt
Bruce Campbell
MOLLY IVINS
ERIK LARSON
GAVIN DE BECKER
Rita Mae Brown
Alice Randall
ALEXANDER MCCALL SMITH
Keri Hulme
Boris Starling
Kathleen O'Neal Gear
William Golding
Robert Graves
William Burroughs
Barbara Vine
Joseph Conrad
William Boyd
Thomas Hardy
E.M. Forster
P J Orourke
Kathy Lette
GABRIE

Lynne Hinton
MICHAEL PALMER
Karen Robards
Joe McGinniss
Angela Elwell Hunt
F. Scott Fritzgerald
Debbie MacOmber
Lisa Carey
Lee Strobel
Frederick Douglass
Andrew Weil
Lloyd Alexander
Maryanne Vollers
Ahdaf Soueif
Martha Cooley
Adele Faber
Anne Wilson Schaef
Karen Kingston
Petru Popescu
Monica Ali
James F., Md. Balch
Ellen Fein
Bill Phillips
Diana Wynne Jones
Margaret Peterson Haddix
Bill O'Reilly
Jim Crace
Rebbecca Ray
ROSALIND MILES
Gregory Benford
Laurence Yep
Sylvia Cassedy
Rand Miller
WILLIAM FAULKNER
Ann Rinaldi
Elisabeth Robinson
Moser Mark Stewart
Robert C. O'Brien
Anchee Min
Magnus Mills
AZAR NAFISI
Wilbur A. Smith
DC Talk
Art Spiegelman
WILLIAM GIBSON
Todd Strasser
Oswald Wynd
Ethan Black
Stanislaw Lem
Nikki Gemmell
Martha Beck
Lawrence Block
Anatolian Treasures
V. C. Andrews
George Lucas
Kathleen E. Woodiwiss
Robert Shea
Graham Greene
GARY PAULSEN
Stephen W. Frey
William Sutcliffe
Ken Weber
ROBERT LOUIS STEVENSON
DAVID LISS
Kage Baker
Gao Xingjian
Robert Fisher
PETER MAYLE
W. 

In [246]:
top_authors[203075]

[u'Toni Morrison',
 u'Sylvia Plath',
 u'Shel Silverstein',
 u'Scott Adams',
 u'RAY BRADBURY']

## Getting top 3 books by top 3 authors

In [247]:
rec_books_by_author = {}
for userid in set(top_authors.keys()):
    if userid not in rec_books_by_author.keys():
        rec_books_by_author[userid] = []
    k = 0
    for author in top_authors[userid][:5]:
        rec_books = list(set(author_data[author]))[:5]
        for isbn, rating in rec_books:
            temp_dict = {}
            if check_in_history(isbn, userid) == 0:
                continue
            bookdetails = get_book_details(isbn)
            temp_dict = bookdetails
            temp_dict['average_rating'] = rating

            rec_books_by_author[userid].append(temp_dict)
#             rec_books_by_author[userid]
                                    

In [248]:
rec_books_by_author.keys()

[241666,
 32773,
 249862,
 67591,
 182969,
 174092,
 204813,
 30735,
 270352,
 116758,
 178199,
 178201,
 126693,
 266268,
 172061,
 229409,
 32802,
 249894,
 194600,
 145449,
 36907,
 247852,
 243759,
 65584,
 129074,
 8245,
 57398,
 143415,
 53304,
 81977,
 129084,
 8253,
 153662,
 52917,
 204864,
 69697,
 245827,
 227397,
 268300,
 10314,
 120908,
 67663,
 184401,
 131154,
 14422,
 260183,
 210959,
 136326,
 139359,
 206944,
 22625,
 6242,
 225379,
 96357,
 125031,
 184424,
 278633,
 6251,
 125039,
 159858,
 157811,
 194676,
 153718,
 227447,
 14456,
 41084,
 138602,
 168064,
 86145,
 196738,
 141444,
 163973,
 213126,
 98440,
 258185,
 94347,
 63854,
 51350,
 127129,
 180378,
 1733,
 213150,
 261829,
 51365,
 155014,
 252071,
 116904,
 86189,
 229551,
 123056,
 6323,
 114868,
 141493,
 135351,
 96440,
 14521,
 86202,
 182459,
 104636,
 272573,
 96448,
 184513,
 55490,
 73923,
 55492,
 55493,
 223431,
 276680,
 274634,
 223438,
 10447,
 135376,
 47316,
 123094,
 123095,
 104665,
 27

In [250]:
rec_books_by_author[70052]

[{'BookAuthor': u'Amy Tan',
  'BookTitle': u'The Hundred Secret Senses',
  'ISBN': u'0399141146',
  'ImageURL': u'http://images.amazon.com/images/P/0399141146.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0399141146.01.MZZZZZZZ.jpg',
  'Publisher': u'Putnam Pub Group',
  'YearOfPublication': 1995,
  'average_rating': 8.083333333333334},
 {'BookAuthor': u'Amy Tan',
  'BookTitle': u'The Joy Luck Club',
  'ISBN': u'0804106304',
  'ImageURL': u'http://images.amazon.com/images/P/0804106304.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0804106304.01.MZZZZZZZ.jpg',
  'Publisher': u'Prentice Hall (K-12)',
  'YearOfPublication': 1994,
  'average_rating': 8.21951219512195,
  'votes': 5},
 {'BookAuthor': u'Amy Tan',
  'BookTitle': u"The Bonesetter's Daughter",
  'ISBN': u'0804114986',
  'ImageURL': u'http://images.amazon.com/images/P/0804114986.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0804114986.01.MZZZZZZZ.jpg',
  'Publish

In [238]:
rec_books_by_author[47316]

[{'BookAuthor': u'Patricia C. Wrede',
  'BookTitle': u'Dealing With Dragons (Enchanted Forest Chronicles (Paperback))',
  'ISBN': u'0590457225',
  'ImageURL': u'http://images.amazon.com/images/P/0590457225.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0590457225.01.MZZZZZZZ.jpg',
  'Publisher': u'Scholastic',
  'YearOfPublication': 1992,
  'average_rating': 8.333333333333334},
 {'BookAuthor': u'Patricia C. Wrede',
  'BookTitle': u'Talking to Dragons (Enchanted Forest Chronicles (Paperback))',
  'ISBN': u'0590484753',
  'ImageURL': u'http://images.amazon.com/images/P/0590484753.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0590484753.01.MZZZZZZZ.jpg',
  'Publisher': u'Point Fantasy',
  'YearOfPublication': 1995,
  'average_rating': 8.0},
 {'BookAuthor': u'Michael Ende',
  'BookTitle': u'Die unendliche Geschichte: Von A bis Z',
  'ISBN': u'3522128001',
  'ImageURL': u'http://images.amazon.com/images/P/3522128001.01.LZZZZZZZ.jpg',
  'ImageURLM

In [239]:
user_history[223231]

[{'BookAuthor': u'Karen Cushman',
  'BookTitle': u'Catherine, Called Birdy (Trophy Newbery)',
  'ISBN': u'0064405842',
  'ImageURL': u'http://images.amazon.com/images/P/0064405842.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0064405842.01.MZZZZZZZ.jpg',
  'Publisher': u'HarperTrophy',
  'YearOfPublication': 1995,
  'average_rating': 8.4},
 {'BookAuthor': u'Karen Cushman',
  'BookTitle': u"The Midwife's Apprentice (Trophy Newbery)",
  'ISBN': u'006440630X',
  'ImageURL': u'http://images.amazon.com/images/P/006440630X.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/006440630X.01.MZZZZZZZ.jpg',
  'Publisher': u'HarperTrophy',
  'YearOfPublication': 1996,
  'average_rating': 7.285714285714286},
 {'BookAuthor': u'Michael Ende',
  'BookTitle': u'The Neverending Story',
  'ISBN': u'0140386335',
  'ImageURL': u'http://images.amazon.com/images/P/0140386335.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0140386335.01.MZZZZZZZ.jpg

In [251]:
import json
with open("rec_books_by_author.json" , "wb") as file:
    file.write(json.dumps(rec_books_by_author))

In [123]:
users_df = pd.read_csv("BX-Users.csv", sep = ';', error_bad_lines = False, encoding = 'latin-1')

In [124]:
users_data = dataset.merge(users_df, on = 'User-ID')

In [30]:
users_data.head()

Unnamed: 0  User-ID        ISBN  Book-Rating               Location   Age
0        1456   277427  002542730X           10  gilbert, arizona, usa  48.0
1        1465   277427  0060542128            7  gilbert, arizona, usa  48.0
2        1474   277427  0061009059            9  gilbert, arizona, usa  48.0
3        1522   277427  0316776963            8  gilbert, arizona, usa  48.0
4        1543   277427  0345413903           10  gilbert, arizona, usa  48.0

In [31]:
users_data['age_group'] = pd.qcut(users_data['Age'], 10)

In [32]:
list(pd.qcut(users_data['Age'], 10).unique()

SyntaxError: unexpected EOF while parsing (<ipython-input-32-ba927908a41e>, line 1)

In [35]:
# [(i, j) for i, j in users_data['age_group'].unique()]
np.array(users_data['age_group'].unique())

array([Interval(47.0, 51.0, closed='right'),
       Interval(51.0, 201.0, closed='right'), nan,
       Interval(0.999, 25.0, closed='right'),
       Interval(28.0, 30.0, closed='right'),
       Interval(25.0, 28.0, closed='right'),
       Interval(43.0, 47.0, closed='right'),
       Interval(38.0, 43.0, closed='right'),
       Interval(30.0, 32.0, closed='right'),
       Interval(34.0, 38.0, closed='right'),
       Interval(32.0, 34.0, closed='right')], dtype=object)

In [36]:
users_data.head()

Unnamed: 0  User-ID        ISBN  Book-Rating               Location   Age  \
0        1456   277427  002542730X           10  gilbert, arizona, usa  48.0   
1        1465   277427  0060542128            7  gilbert, arizona, usa  48.0   
2        1474   277427  0061009059            9  gilbert, arizona, usa  48.0   
3        1522   277427  0316776963            8  gilbert, arizona, usa  48.0   
4        1543   277427  0345413903           10  gilbert, arizona, usa  48.0   

      age_group  
0  (47.0, 51.0]  
1  (47.0, 51.0]  
2  (47.0, 51.0]  
3  (47.0, 51.0]  
4  (47.0, 51.0]

## Age group data

In [34]:
age_group_data = {}
temp_data = users_data[['ISBN', 'age_group']]
# print temp_data
for isbn, age_group in temp_data.values:
    if str(age_group) not in age_group_data.keys():
        age_group_data[str(age_group)] = {}
    if isbn in age_group_data[str(age_group)].keys():
        age_group_data[str(age_group)][isbn] += 1
    else : age_group_data[str(age_group)][isbn] = 1


In [48]:
rec_books_by_age = {}
for age_group in age_group_data.keys():
#     print sorted(age_group_data[age_group].items(), key=lambda x:x[1], reverse = True)
    temp_list = sorted(age_group_data[age_group].items(), key=lambda x:x[1], reverse = True)
    top_isbn = [(isbn, votes) for isbn, votes in temp_list[:min(14, len(temp_list))]]
    rec_books_by_age[age_group] = []
    for isbn, votes in top_isbn:
#         if check_in_history(isbn, user_id) == 0:
#             print isbn, user_id
#             continue
        book_details = get_book_details(isbn)
        temp_dict = book_details
        temp_dict['votes'] = votes
        rec_books_by_age[age_group].append(temp_dict)
#     print rec_books_by_age
#     break
del rec_books_by_age['nan']

In [37]:
rec_books_by_age['(38.0, 43.0]']

[{'BookAuthor': u'Sue Monk Kidd',
  'BookTitle': u'The Secret Life of Bees',
  'ISBN': u'0142001740',
  'ImageURL': u'http://images.amazon.com/images/P/0142001740.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0142001740.01.MZZZZZZZ.jpg',
  'Publisher': u'Penguin Books',
  'YearOfPublication': 2003,
  'votes': 6},
 {'BookAuthor': u'Alice Sebold',
  'BookTitle': u'The Lovely Bones: A Novel',
  'ISBN': u'0316666343',
  'ImageURL': u'http://images.amazon.com/images/P/0316666343.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0316666343.01.MZZZZZZZ.jpg',
  'Publisher': u'Little, Brown',
  'YearOfPublication': 2002,
  'votes': 12},
 {'BookAuthor': u'Dan Brown',
  'BookTitle': u'Angels &amp; Demons',
  'ISBN': u'0671027360',
  'ImageURL': u'http://images.amazon.com/images/P/0671027360.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0671027360.01.MZZZZZZZ.jpg',
  'Publisher': u'Pocket Star',
  'YearOfPublication': 2001,
  'votes'

In [56]:
len(users_data[['User-ID', 'age_group']].values)

37548

In [58]:
subdata = users_data[['User-ID', 'age_group']].values
age_recommendations_final = {}
for userid, agegroup in subdata:
    if str(agegroup) in rec_books_by_age.keys():
        temp_list = []
        for book_info in rec_books_by_age[str(agegroup)]:
#             print check_in_
#             print user_id
            if check_in_history(book_info['ISBN'], userid) == 1:
                temp_list.append(book_info)
        age_recommendations_final[userid] = temp_list
    else:
        age_recommendations_final[userid] = best_books_details
        u = userid
#         break

 {'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ba

{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ban

{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ban

{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http:

{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http://images.amazon.com/images/P/0440998050.01.MZZZZZZZ.jpg', 'ISBN': u'0440998050', 'BookAuthor': u"Madeleine L'Engle", 'BookTitle': u'A Wrinkle in Time', 'votes': 5, 'YearOfPublication': 1976, 'ImageURL': u'http://images.amazon.com/images/P/0440998050.01.LZZZZZZZ.jpg'}
{'Publisher': u'Laure Leaf', 'ImageURLM': u'http:

{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ban

{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ban

{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Bantam', 'ImageURLM': u'http://images.amazon.com/images/P/0553296981.01.MZZZZZZZ.jpg', 'ISBN': u'0553296981', 'BookAuthor': u'ANNE FRANK', 'BookTitle': u'Anne Frank: The Diary of a Young Girl', 'votes': 10, 'YearOfPublication': 1993, 'ImageURL': u'http://images.amazon.com/images/P/0553296981.01.LZZZZZZZ.jpg'}
{'Publisher': u'Ban

10

In [51]:
age_recommendations_final.keys()

[278633, 278026, 277427]

In [218]:
age_recommendations_final

{241666: [{'BookAuthor': u'Alice Sebold',
   'BookTitle': u'The Lovely Bones: A Novel',
   'ISBN': u'0316666343',
   'ImageURL': u'http://images.amazon.com/images/P/0316666343.01.LZZZZZZZ.jpg',
   'ImageURLM': u'http://images.amazon.com/images/P/0316666343.01.MZZZZZZZ.jpg',
   'Publisher': u'Little, Brown',
   'YearOfPublication': 2002,
   'votes': 12},
  {'BookAuthor': u'John Grisham',
   'BookTitle': u'The Firm',
   'ISBN': u'044021145X',
   'ImageURL': u'http://images.amazon.com/images/P/044021145X.01.LZZZZZZZ.jpg',
   'ImageURLM': u'http://images.amazon.com/images/P/044021145X.01.MZZZZZZZ.jpg',
   'Publisher': u'Bantam Dell Publishing Group',
   'YearOfPublication': 1992,
   'votes': 6},
  {'BookAuthor': u'Andre Dubus III',
   'BookTitle': u'House of Sand and Fog',
   'ISBN': u'0375727345',
   'ImageURL': u'http://images.amazon.com/images/P/0375727345.01.LZZZZZZZ.jpg',
   'ImageURLM': u'http://images.amazon.com/images/P/0375727345.01.MZZZZZZZ.jpg',
   'Publisher': u'Vintage Books',

In [117]:
with open("rec_books_by_age.json" , "wb") as file:
    file.write(json.dumps(age_recommendations_final))

In [224]:
subdata = users_data[['ISBN', 'Location']].values
location_data = {}
for isbn, location in subdata:
    if location not in location_data.keys():
        location_data[location] = {}
    if isbn not in location_data[location]:
        location_data[location][isbn] = 0
    location_data[location][isbn] += 1

In [228]:
location_data.keys()[1]

u'n/a, british columbia, canada'

In [262]:
location_data['lafayette, indiana, usa']

{'0064403319': 1,
 '0064407675': 1,
 '015216250X': 1,
 '0345368754': 1,
 '0380709538': 1,
 '0380789019': 1,
 '0380791978': 1,
 '0380816555': 1,
 '0440418321': 1,
 '0446515078': 1,
 '0446519723': 1,
 '0446525537': 1,
 '0451187903': 1,
 '0451456718': 1,
 '0553213148': 1,
 '0553213180': 1,
 '0553269224': 1,
 '0553280414': 1,
 '0590457225': 1,
 '0590484753': 1,
 '0689710895': 1,
 '0689711522': 1,
 '0743412028': 1}

In [230]:
users_data['User-ID'].unique()

Unnamed: 0  User-ID        ISBN  Book-Rating               Location   Age  \
0        1456   277427  002542730X           10  gilbert, arizona, usa  48.0   
1        1465   277427  0060542128            7  gilbert, arizona, usa  48.0   
2        1474   277427  0061009059            9  gilbert, arizona, usa  48.0   
3        1522   277427  0316776963            8  gilbert, arizona, usa  48.0   
4        1543   277427  0345413903           10  gilbert, arizona, usa  48.0   

      age_group  
0  (47.0, 51.0]  
1  (47.0, 51.0]  
2  (47.0, 51.0]  
3  (47.0, 51.0]  
4  (47.0, 51.0]

In [233]:
subdata = users_data[['User-ID', 'Location', 'Age', 'age_group']]

In [245]:
user_data_dict = {}
for i in range(len(subdata)):
    userid , loc, agegroup = subdata.loc[i, ['User-ID', 'Location', 'age_group']]
    print agegroup
    user_data_dict[userid] = {}
    user_data_dict[userid]['Location'] = loc
    user_data_dict[userid]['age_group'] = str(agegroup)
#     print user_data_dict
    
#     break
# for userid, location, agegroup in subdata.values:
#     user_data_dict['userid'] = userid
#     user_data_dict['Location'] = location
#     user_data_dict['agegroup'] = agegroup
    

(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0

(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
(47.0, 51.0]
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 28.0]
(25.0, 2

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(43.0, 47.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0,

...

(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999

(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
(34.0, 38.0]
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0, 32.0]
(30.0

(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]
(32.0, 34.0]

(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43.0]
(38.0, 43

(43.0, 47.0]
(43.0, 47.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(28.0, 30.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
(0.999, 25.0]
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]
(51.0, 201.0]


In [246]:
subdata['Location'].value_counts()

n/a, n/a, n/a                         1884
toronto, ontario, canada               681
mechanicsville, maryland, usa          625
chicago, illinois, usa                 436
calgary, alberta, canada               366
charleston, west virginia, usa         360
honolulu, hawaii, usa                  335
seattle, washington, usa               322
morrow, georgia, usa                   305
topeka, kansas, usa                    296
ft. stewart, georgia, usa              292
san antonio, texas, usa                264
youngstown, ohio, usa                  261
st. louis, missouri, usa               251
london, england, united kingdom        251
simi valley, california, usa           230
orlando, florida, usa                  220
portland, oregon, usa                  207
edmonton, alberta, canada              201
san jose, california, usa              201
tulsa, oklahoma, usa                   199
new york, new york, usa                196
alvin, texas, usa                      193
cleveland, 

In [291]:
[str(i) for i in users_data['age_group'].unique()]

['(47.0, 51.0]',
 '(51.0, 201.0]',
 'nan',
 '(0.999, 25.0]',
 '(28.0, 30.0]',
 '(25.0, 28.0]',
 '(43.0, 47.0]',
 '(38.0, 43.0]',
 '(30.0, 32.0]',
 '(34.0, 38.0]',
 '(32.0, 34.0]']

In [277]:
rec_data_by_location = {}
for loc in location_data.keys():
#     print location_data[loc]
    data = sorted(location_data[loc].items(), key=lambda x:x[1], reverse = True)
    rec_data_by_location[loc] = []
    for isbn, votes in data[:min(10, len(data))]:
        book_details = get_book_details(isbn)
        temp_dict = book_details
        temp_dict['votes'] = votes
        rec_data_by_location[loc].append(temp_dict)
#     print rec_data_by_location

In [282]:
rec_data_by_location[rec_data_by_location.keys()[0]]

[{'BookAuthor': u'Nicholas Sparks',
  'BookTitle': u'The Notebook',
  'ISBN': u'0446605239',
  'ImageURL': u'http://images.amazon.com/images/P/0446605239.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0446605239.01.MZZZZZZZ.jpg',
  'Publisher': u'Warner Books',
  'YearOfPublication': 1998,
  'predited_rating': 10,
  'votes': 1},
 {'BookAuthor': u'George Orwell',
  'BookTitle': u'Animal Farm',
  'ISBN': u'0451526341',
  'ImageURL': u'http://images.amazon.com/images/P/0451526341.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0451526341.01.MZZZZZZZ.jpg',
  'Publisher': u'Signet',
  'YearOfPublication': 2004,
  'votes': 1},
 {'BookAuthor': u'David Baldacci',
  'BookTitle': u'Saving Faith',
  'ISBN': u'0446608890',
  'ImageURL': u'http://images.amazon.com/images/P/0446608890.01.LZZZZZZZ.jpg',
  'ImageURLM': u'http://images.amazon.com/images/P/0446608890.01.MZZZZZZZ.jpg',
  'Publisher': u'Warner Vision',
  'YearOfPublication': 2000,
  'votes': 1},


In [278]:
subdata = users_data[['User-ID', 'Location']]

In [280]:
subdata.values

array([[277427, u'gilbert, arizona, usa'],
       [277427, u'gilbert, arizona, usa'],
       [277427, u'gilbert, arizona, usa'],
       ...,
       [276680, u'hopewell junction, new york, usa'],
       [276680, u'hopewell junction, new york, usa'],
       [276680, u'hopewell junction, new york, usa']], dtype=object)

In [298]:
rec_data_by_location_final = {}
k = 0
    for user_id, location in subdata.values:
    temp_list = []
#     print rec_data_by_location[location]
    for book in rec_data_by_location[location]:
        if check_in_history(book['ISBN'], user_id) == 1:
            temp_list.append(book)
    rec_data_by_location_final[user_id] = temp_list
    print rec_data_by_location_final
    print ''
    if k == 1 : break
    k = 1

{'Publisher': u'Pocket Star', 'ImageURLM': u'http://images.amazon.com/images/P/0743457943.01.MZZZZZZZ.jpg', 'ISBN': u'0743457943', 'BookAuthor': u'Fern Michaels', 'BookTitle': u'Trading Places', 'predited_rating': 10, 'votes': 1, 'YearOfPublication': 2003, 'ImageURL': u'http://images.amazon.com/images/P/0743457943.01.LZZZZZZZ.jpg'}
{'Publisher': u'Andrews McMeel Publishing', 'ImageURLM': u'http://images.amazon.com/images/P/0836221192.01.MZZZZZZZ.jpg', 'ISBN': u'0836221192', 'BookAuthor': u'Scott Adams', 'BookTitle': u'Dilbert Fugitive From The Cubicle Police', 'predited_rating': 10, 'votes': 1, 'YearOfPublication': 1996, 'ImageURL': u'http://images.amazon.com/images/P/0836221192.01.LZZZZZZZ.jpg'}
{'Publisher': u'HarperTorch', 'ImageURLM': u'http://images.amazon.com/images/P/0060542128.01.MZZZZZZZ.jpg', 'ISBN': u'0060542128', 'BookAuthor': u'Heather Lowell', 'BookTitle': u'When the Storm Breaks', 'predited_rating': 10, 'votes': 1, 'YearOfPublication': 2003, 'ImageURL': u'http://images.a

In [285]:
len(rec_data_by_location_final)

1117

In [286]:
with open("rec_books_by_location.json", "wb") as file:
    file.write(json.dumps(rec_data_by_location_final))

In [17]:
with open("user_history.pickle" , "wb") as file:
    pickle.dump(user_history, file)

In [249]:
from faker import Faker
fake = Faker()

In [251]:
from datetime import datetime

datetime_start = datetime.strptime('Sep 8 2018', '%b %d %Y')
datetime_end = datetime.strptime('Sep 8 2020', '%b %d %Y')

In [252]:
fake.date_between_dates(date_start=datetime_start, date_end=datetime_end).strftime("%d %B %Y")

'22 December 2019'

In [253]:
fake.phone_number()
fake.ascii_email()

u'zsmith@ellis.com'

In [258]:
final_data = []
for user_id in recommendation_data:
    fake = Faker()
    user_data = {}
    user_data['user_id'] = user_id
    user_data['name'] = fake.name()
    if user_id not in user_data_dict.keys() or 'n/a, n/a, n/a' == user_data_dict[user_id]['Location']:
        user_data['address'] = fake.address()
    else:
        user_data['address'] = user_data_dict[user_id]['Location']
    
    random_date = fake.date_between_dates(date_start=datetime_start, date_end=datetime_end).strftime("%d %B %Y")
    user_data['expiry_date'] = random_date
    user_data['email'] = fake.ascii_email()
    user_data['age_group'] = user_data_dict[user_id]['age_group']
    user_data['user_password'] = user_id
    user_data['history'] = user_history[user_id]
    user_data['recommended_books'] = []
    recommended_books = recommendation_data[user_id]
    for isbn, rating in recommended_books:
        book_details = get_book_details(isbn)
        book_details['predited_rating'] = rating
        user_data['recommended_books'].append(book_details)
        
#     for i in user_data['history']:
#         print i
#         break
#     break

    final_data.append(user_data)

#     farzi = user_data['recommended_books']
#     farzi =  user_data
#     break
#     recommendation_data[user_id]
#     user_past_books = user_history[user_id]

In [255]:
len(final_data)

1117

In [24]:
dataset.head()

Unnamed: 0  User-ID        ISBN  Book-Rating
0        1456   277427  002542730X           10
1        1465   277427  0060542128            7
2        1474   277427  0061009059            9
3        1522   277427  0316776963            8
4        1543   277427  0345413903           10

In [25]:
final_data[90]['user_id']

114988

In [26]:
a = [i['ISBN'] for i in final_data[90]['history']]

In [57]:
for user_data in range(len(final_data)):
    rec_data = recommendation_data[final_data[user_data]['user_id']]
#     print rec_data
    rec_data_final = []
    for isbn, predicted_rating in rec_data:
        book_details = get_book_details(isbn)
        book_details['predicted_rating'] = predicted_rating
        rec_data_final.append(book_details)
    print rec_data_final
    print final_data[user_data]['user_id']
    final_data[user_data]['recommended_books'] = rec_data_final
    break
#     final_data[]
#     break
#     break
    

[{'Publisher': u'Doubleday Books', 'ImageURLM': u'http://images.amazon.com/images/P/0385420161.01.MZZZZZZZ.jpg', 'ISBN': u'0385420161', 'BookAuthor': u'Laura Esquivel', 'BookTitle': u'Like Water for Chocolate: A Novel in Monthly Installments, With Recipes, Romances, and Home Remedies', 'predited_rating': 10, 'YearOfPublication': 1992, 'predicted_rating': 10, 'ImageURL': u'http://images.amazon.com/images/P/0385420161.01.LZZZZZZZ.jpg'}, {'Publisher': u'Roc', 'ImageURLM': u'http://images.amazon.com/images/P/0451456734.01.MZZZZZZZ.jpg', 'ISBN': u'0451456734', 'BookAuthor': u'Anne Bishop', 'BookTitle': u'Queen of the Darkness (Black Jewels Trilogy)', 'predited_rating': 10, 'YearOfPublication': 2000, 'predicted_rating': 10, 'ImageURL': u'http://images.amazon.com/images/P/0451456734.01.LZZZZZZZ.jpg'}, {'Publisher': u'Daw Books', 'ImageURLM': u'http://images.amazon.com/images/P/0886774632.01.MZZZZZZZ.jpg', 'ISBN': u'0886774632', 'BookAuthor': u'Mercedes Lackey', 'BookTitle': u"By the Sword (Ke

In [29]:
import json
with open("final_data_knn_zscore.json", "wb") as file:
    file.write(json.dumps(final_data))

In [30]:
import json 
with open("sample_data__knn_zscore.json", "wb") as file:
    file.write(json.dumps(final_data[4:6]))

In [259]:
import json
with open("final_data_knn_zscore_final.json", "wb") as file:
    file.write(json.dumps(final_data))

In [257]:
import pickle
with open("predictions_zscore_final.pickle", "rb") as file:
    a = pickle.load(file)

IOError: [Errno 2] No such file or directory: 'predictions_zscore_final.pickle'

In [5]:
a[241666]

[('0385420161', 10),
 ('0451456734', 10),
 ('0886774632', 10),
 ('0671527215', 10),
 ('0671876015', 10),
 ('0060930187', 10),
 ('0553560247', 10),
 ('0140280553', 10),
 ('0872860175', 10),
 ('0449213447', 10)]

In [9]:
df.head()

ISBN                                         Book-Title  \
0  0195153448                                Classical Mythology   
1  0002005018                                       Clara Callan   
2  0060973129                               Decision in Normandy   
3  0374157065  Flu: The Story of the Great Influenza Pandemic...   
4  0393045218                             The Mummies of Urumchi   

            Book-Author Year-Of-Publication                   Publisher  \
0    Mark P. O. Morford                2002     Oxford University Press   
1  Richard Bruce Wright                2001       HarperFlamingo Canada   
2          Carlo D'Este                1991             HarperPerennial   
3      Gina Bari Kolata                1999        Farrar Straus Giroux   
4       E. J. W. Barber                1999  W. W. Norton &amp; Company   

                                         Image-URL-S  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-M  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-L  
0  http://images.amazon.com/images/P/0195153448.0...  
1  http://images.amazon.com/images/P/0002005018.0...  
2  http://images.amazon.com/images/P/0060973129.0...  
3  http://images.amazon.com/images/P/0374157065.0...  
4  http://images.amazon.com/images/P/0393045218.0...

In [74]:
df[df['ISBN'] == '0195153448']

ISBN            BookTitle          BookAuthor YearOfPublication  \
0  0195153448  Classical Mythology  Mark P. O. Morford              2002   

                 Publisher                                        Image-URL-S  \
0  Oxford University Press  http://images.amazon.com/images/P/0195153448.0...   

                                           ImageURLM  \
0  http://images.amazon.com/images/P/0195153448.0...   

                                            ImageURL  
0  http://images.amazon.com/images/P/0195153448.0...